<h2>Lab 2 - Indexing</h2>

<h4>Preprocessing</h4>

Download the following <a href="">file</a>, which contains: 
- Collection 1: 5 sample 1-line-documents used in lecture 5. 
- Collection 2: 1000 sample news articles. 
    
Note1: there are two versions of the files, XML and TXT. You are free to use the one you want for the lab. However, it worth noting that XML format is the more standard one in TREC IR test collections. 

Note 2: for the news articles collection, please include the headline of the article to the index. 

Note 3: these are very small collections just for experimentation
    
Be sure that you have your preprocessing module ready (revise: lab 1), then apply it to the collections. 
if you didn't have it done, then at least get the tokeniser and casefolding ready for this lab

In [1]:
# imports go here
import matplotlib.pyplot as plt
from stemming.porter2 import stem
import os
import re
import xml.etree.ElementTree as ElementTree

In [2]:
# preprocessing functions
def preprocess(text, docNo, stopword_file='./englishST.txt', stemming=True, stopping=True):
    words = []
    
    # [^\w\s]|_ -> match a single character not present in the [\w\s] list
    # \w matches any word character (equal to [a-zA-Z0-9_]
    # \s matches any whitespace character (equal to [\r\n\t\f\v ]
    # 2nd alternative - match underscore
    # so this regex will look for any non-letter, non-digit character and replace it with a space
    text = re.sub(r"[^\w\s]|_", " ", text).split()
    if len(text) > 0:
        # add all the words to a list
        words.extend(list(zip(text, [docNo]*len(text), range(len(text)))))
    
    # lowercase
    words = [(word[0].lower(), word[1], word[2]) for word in words]
    
    if stopping:
        # remove all english stopwords
        # read all the stopwords into a list
        with open(stopword_file) as f:
            stopwords = f.read().split()

        f.close()

        # remove all words that are in the stopwords list
        clean_words = []
        for word in words:
            if word[0] not in stopwords:
                clean_words.append(word)
    else:
        clean_words = words
    
    if stemming:
        # stemming
        stemmed_words = [(stem(word[0]), word[1], word[2]) for word in clean_words]
    else:
        stemmed_words = clean_words

    # this will return a list of tuples
    # (elem, position)
    # where elem = (word, docID)
    return stemmed_words

<h4>Positional Inverted Index</h4>

Implement positional inverted index. You need to save the following information in terms inverted lists: 
- term (pre-processed) and its document frequency (optional) 
- list of documents where this term occured 
- for each document, list of positions where the term occured within the document

Print output in a text file for visualisation. Example output here (examples didn't apply stopping or stemming) 
in practice (for assignment), you might save in a more effecient format (e.g. binary files).
Please check the output inverted index when enable/disable the following: 
- stopping 
- stemming

In [3]:
with open('./collections/sample.xml', 'r') as f:   # Reading file
    xml = f.read()

xml = '<ROOT>' + xml + '</ROOT>'   # Let's add a root tag

root = ElementTree.fromstring(xml)
word_list = []

# Simple loop through each document
for doc in root:
    for elem in doc:
        if elem.tag.lower() == 'docno':
            docNo = elem.text.strip()
        elif elem.tag.lower() == 'text':
            text = elem.text.strip()
            # preprocess the text 
            preprocessed_text = preprocess(text, docNo, stemming=False, stopping=False)
            word_list.extend(preprocessed_text)
        elif elem.tag.lower() == 'headline':
            headline = elem.text.strip()
            # preprocess the headline
            preprocessed_headline = preprocess(headline, docNo)
            word_list.extend(preprocessed_headline)

            
print(word_list)

[('he', '1', 0), ('likes', '1', 1), ('to', '1', 2), ('wink', '1', 3), ('he', '1', 4), ('likes', '1', 5), ('to', '1', 6), ('drink', '1', 7), ('he', '2', 0), ('likes', '2', 1), ('to', '2', 2), ('drink', '2', 3), ('and', '2', 4), ('drink', '2', 5), ('and', '2', 6), ('drink', '2', 7), ('the', '3', 0), ('thing', '3', 1), ('he', '3', 2), ('likes', '3', 3), ('to', '3', 4), ('drink', '3', 5), ('is', '3', 6), ('ink', '3', 7), ('the', '4', 0), ('ink', '4', 1), ('he', '4', 2), ('likes', '4', 3), ('to', '4', 4), ('drink', '4', 5), ('is', '4', 6), ('pink', '4', 7), ('he', '5', 0), ('likes', '5', 1), ('to', '5', 2), ('wink', '5', 3), ('and', '5', 4), ('drink', '5', 5), ('pink', '5', 6), ('ink', '5', 7)]


In [4]:
# sort the word list
word_list = sorted(word_list)
print(word_list)

[('and', '2', 4), ('and', '2', 6), ('and', '5', 4), ('drink', '1', 7), ('drink', '2', 3), ('drink', '2', 5), ('drink', '2', 7), ('drink', '3', 5), ('drink', '4', 5), ('drink', '5', 5), ('he', '1', 0), ('he', '1', 4), ('he', '2', 0), ('he', '3', 2), ('he', '4', 2), ('he', '5', 0), ('ink', '3', 7), ('ink', '4', 1), ('ink', '5', 7), ('is', '3', 6), ('is', '4', 6), ('likes', '1', 1), ('likes', '1', 5), ('likes', '2', 1), ('likes', '3', 3), ('likes', '4', 3), ('likes', '5', 1), ('pink', '4', 7), ('pink', '5', 6), ('the', '3', 0), ('the', '4', 0), ('thing', '3', 1), ('to', '1', 2), ('to', '1', 6), ('to', '2', 2), ('to', '3', 4), ('to', '4', 4), ('to', '5', 2), ('wink', '1', 3), ('wink', '5', 3)]


In [5]:
# Split into postings for each word
# This version is just a dictionary of dictinaries
inverted_index = dict()

for elem in word_list:
    word = elem[0]
    docNo = elem[1]
    position = elem[2]
    #print("Word: {0}, docNo: {1}, position: {2}".format(word, docNo, position))
    
    if word in inverted_index.keys():
        #print("Word in index!")
        if docNo in inverted_index[word].keys():
            #print("Doc in index!")
            inverted_index[word][docNo].append(position)
        else:
            #print("Doc not in index")
            inverted_index[word][docNo] = [position]
    else:
        #print("Word not in index!")
        inverted_index[word] = {docNo: [position]}


In [6]:
inverted_index

{'and': {'2': [4, 6], '5': [4]},
 'drink': {'1': [7], '2': [3, 5, 7], '3': [5], '4': [5], '5': [5]},
 'he': {'1': [0, 4], '2': [0], '3': [2], '4': [2], '5': [0]},
 'ink': {'3': [7], '4': [1], '5': [7]},
 'is': {'3': [6], '4': [6]},
 'likes': {'1': [1, 5], '2': [1], '3': [3], '4': [3], '5': [1]},
 'pink': {'4': [7], '5': [6]},
 'the': {'3': [0], '4': [0]},
 'thing': {'3': [1]},
 'to': {'1': [2, 6], '2': [2], '3': [4], '4': [4], '5': [2]},
 'wink': {'1': [3], '5': [3]}}

In [7]:
# print inverted index to file
for word in inverted_index.keys():
    print(word + ":")
    for docNo in inverted_index[word].keys():
        print("\t" + docNo + ":" + ", ".join(str(i) for i in inverted_index[word][docNo]))

and:
	2:4, 6
	5:4
drink:
	1:7
	2:3, 5, 7
	3:5
	4:5
	5:5
he:
	1:0, 4
	2:0
	3:2
	4:2
	5:0
ink:
	3:7
	4:1
	5:7
is:
	3:6
	4:6
likes:
	1:1, 5
	2:1
	3:3
	4:3
	5:1
pink:
	4:7
	5:6
the:
	3:0
	4:0
thing:
	3:1
to:
	1:2, 6
	2:2
	3:4
	4:4
	5:2
wink:
	1:3
	5:3


<h4>Refactoring</h4>

Pack all these up into a function

In [108]:
def build_inverted_index(input_file, stopword_file='./englishST.txt', stemming=True, stopping=True):
    
    with open(input_file, 'r') as f:   # Reading file
        xml = f.read()

        xml = '<ROOT>' + xml + '</ROOT>'   # Let's add a root tag

        root = ElementTree.fromstring(xml)
        word_list = []

        # Simple loop through each document
        for doc in root:
            for elem in doc:
                if elem.tag.lower() == 'docno':
                    docNo = int(elem.text.strip())
                elif elem.tag.lower() == 'text':
                    text = elem.text.strip()
                    # preprocess the text 
                    preprocessed_text = preprocess(text, docNo, stopword_file, stemming, stopping)
                    word_list.extend(preprocessed_text)
                elif elem.tag.lower() == 'headline':
                    headline = elem.text.strip()
                    # preprocess the headline
                    preprocessed_headline = preprocess(headline, docNo, stopword_file, stemming, stopping)
                    word_list.extend(preprocessed_headline)
    
    # sort the word list
    word_list = sorted(word_list)
    
    # Split into postings for each word
    # This version is just a dictionary of dictinaries
    inverted_index = dict()

    for elem in word_list:
        word = elem[0]
        docNo = elem[1]
        position = elem[2]
        #print("Word: {0}, docNo: {1}, position: {2}".format(word, docNo, position))

        if word in inverted_index.keys():
            #print("Word in index!")
            if docNo in inverted_index[word].keys():
                #print("Doc in index!")
                inverted_index[word][docNo].append(position)
            else:
                #print("Doc not in index")
                inverted_index[word][docNo] = [position]
        else:
            #print("Word not in index!")
            inverted_index[word] = {docNo: [position]}
    
    # print inverted index to file
    for word in inverted_index.keys():
        print(word + ":")
        for docNo in inverted_index[word].keys():
            print("\t" + str(docNo) + ":" + ", ".join(str(i) for i in inverted_index[word][docNo]))
    
    return inverted_index

In [109]:
build_inverted_index('./collections/trec.sample.xml')

0:
	14:89, 193, 208, 219
	15:18, 38, 43, 505
	21:274, 284
	23:250
	37:23, 84, 206, 226
	59:16, 194, 218, 261, 307, 364, 501, 829, 908, 945, 1002, 1048, 1110, 1147, 1209
	118:220
	128:185
	135:335, 353
	137:1226, 1228
	144:266
	145:384, 545, 600
	146:24, 356, 359, 372, 374, 376, 398, 411, 450, 473, 489, 502, 515, 528, 541, 543, 554, 556, 558, 581, 583, 594, 596, 607, 609, 634, 647, 649, 651, 689, 701, 703
	216:68
	217:35, 187
	222:128
	268:318, 324, 330, 331, 359, 365, 391, 405, 459, 466
	275:346, 399, 419, 433
	287:823, 874, 879, 881, 886, 899, 900, 909, 913, 914, 928, 942, 980, 1004, 1018, 1020, 1023, 1034, 1047, 1048, 1059, 1061, 1067, 1072, 1074, 1107, 1119, 1127, 1139, 1191, 1193, 1211, 1258, 1269, 1301, 1324, 1468, 1515, 1526, 1563, 1571, 1618, 1652, 1655, 1666, 1678, 1685, 1688, 1694, 1699, 1710, 1716, 1721, 1734, 1747, 1753, 1760, 1802, 1806, 1811, 1813, 1836, 1861, 1872, 1884, 1917, 1942, 1946, 1952, 1953, 1964, 1970, 1974, 1975, 1982, 1984, 1989, 2002, 2021, 2046, 2054, 2080, 

	244:194
146p:
	3693:776
	3848:283
147:
	3945:51, 88
147m:
	295:128
148:
	244:218
	3840:102
148m:
	3478:227
149:
	244:255
	3945:64, 74
149m:
	3478:234
149p:
	141:904
14bn:
	3808:188
14m:
	32:26
	138:650
	160:204
	171:11
	184:35
	3331:380
	3439:380
	3611:52
	3715:180
14p:
	351:1923
	3607:60
	3625:394
	3630:262
14s:
	96:157
14th:
	3788:434
15:
	7:12
	13:154
	14:495
	16:362, 1082
	19:464
	32:22
	35:308
	36:14, 147
	39:273
	42:120
	52:36
	55:278, 961
	79:135
	95:88
	129:1003
	133:271, 1478
	136:316, 869
	141:690, 1318
	144:74, 554
	145:381
	146:367, 469, 545, 559, 667, 669, 671, 707
	148:360
	150:81, 84
	154:186
	160:64, 155
	171:209
	185:74
	190:48
	192:127
	194:159
	197:76
	199:191, 339
	210:193
	214:647
	215:20, 88
	217:155
	226:818
	244:135, 256
	248:534
	256:307
	261:141
	269:491
	275:438
	282:314
	287:711, 834, 846, 858, 1623
	312:570
	315:941, 953
	340:302, 467
	341:243
	346:66
	351:84, 145, 622, 693, 970, 1423, 1479, 1658
	357:180
	366:166
	367:584
	369:25
	371:360
	374:150, 529
	3

	3417:520
	3693:1597
	3701:281
2004:
	351:2033
2005:
	188:486
	351:1334
	3417:553
2006:
	351:1522
	3468:196
2007:
	351:1482
	3701:282
2008:
	313:466
2009:
	351:1938
200bn:
	357:28
200m:
	18:76
	36:119
	151:53
	155:113
	201:208
	245:58
	312:304
	313:584
	3386:15
	3389:15
	3406:694
	3409:357
	3435:592
	3450:29
	3484:29
	3571:251
	3578:240
	3700:129
	3716:1190
	3871:346
	3928:506
	3931:831
200mph:
	371:85
200mw:
	3649:145
200p:
	3459:257
	3630:40
201:
	3566:128
2010:
	19:128
	3410:303
	3412:762
	3655:180, 278
2011:
	313:610
	3781:756
2012:
	351:1458
2014:
	3768:266
2015:
	351:1643
201m:
	148:200
2020:
	3417:1024
2024:
	3643:880
2025:
	3417:466
202m:
	3570:750
203:
	128:175
	3695:873
204:
	3353:56
205:
	104:101, 110
	322:205
	356:107
	3529:262
	3694:559
	3792:224
	3826:620
205bn:
	3412:582
206p:
	3606:428
207:
	207:160
	3774:174
207m:
	3477:139
	3715:161
207p:
	32:165
	3459:1334
208:
	3614:76
209:
	3622:288
20bn:
	65:351, 395, 467, 498
	282:115
	3493:304
	3711:152
	3931:231
20m:
	42:31
	26

	3879:66
350m:
	154:361
	3435:936, 965
	3503:1822
	3571:244
	3600:68
350p:
	141:911
	3833:95
352:
	3829:132
352m:
	32:131
353:
	3786:1137
354:
	12:341
3547:
	341:1546
354p:
	3459:926
355:
	3559:51
3550:
	3790:1263
356:
	3530:750
	3774:54
356bn:
	3378:32
357:
	128:52, 54
	3559:53
	3666:232
	3774:52
358:
	128:48
	3559:45
359:
	128:46
	3559:47
	3774:46, 48
35bn:
	298:24, 154
	3814:120
35m:
	184:294
	323:331
	3343:100
	3491:352
	3590:66
	3617:27
	3693:751
	3697:17
	3705:68
	3848:55
35p:
	65:456
	3369:681, 937
	3618:113
	3830:49
35th:
	106:19, 28
36:
	14:388
	53:148
	56:129
	146:435, 592, 680
	169:710
	171:101
	201:281
	244:191
	3343:74
	3412:594
	3436:338
	3477:45
	3530:797
	3551:190
	3591:64
	3628:59
	3644:300, 578
	3694:372
	3709:64
	3715:217
	3716:554
	3789:86
	3808:248
	3891:80
360:
	131:919
	3628:188
	3838:255
360m:
	3382:5
	3570:136
363:
	3524:278
364:
	3380:12
	3574:320
364p:
	3459:1163
366p:
	141:934
367:
	3530:761
369:
	3740:184
	3835:44
36bn:
	312:339
	3323:169
	3716:162
36cts:
	

	327:746
	341:1510
	356:92
	371:794, 833
	374:601
	3336:504
	3362:373
	3377:50
	3388:36, 175, 275
	3390:275
	3397:382
	3410:220
	3416:336
	3417:513
	3420:23, 112
	3441:74
	3468:317
	3470:54
	3485:37
	3525:107
	3527:192
	3547:112
	3551:211
	3570:663
	3571:111
	3577:124
	3585:50
	3599:134
	3604:232
	3606:148
	3642:600, 603
	3655:368
	3663:149
	3680:215
	3693:371
	3697:162
	3706:269, 449
	3786:309, 397
	3788:781
	3790:42
	3792:295
	3793:350
	3808:42
	3826:724
	3856:334
	3857:7, 25, 205
	3867:882
	3879:215
	3886:213, 245, 473
	3892:113
	3895:657
	3912:782
	3921:367
	3928:796
	3932:576
	3935:450
600:
	18:152
	55:882
	59:683
	74:131
	161:137
	177:303
	230:16
	252:139
	265:372
	272:405
	285:81
	334:188
	3369:969
	3435:888
	3569:702
	3570:444
	3574:321
	3641:593
	3662:76
	3828:288
	3837:115
	3923:476, 611
	3927:301
	3931:847
	3939:199
6000:
	129:872
	3919:535
	3921:400, 522, 626
	3936:954
60000:
	3933:988
600ft:
	3426:26
600m:
	141:542
	3434:539
	3463:984
	3587:376
	3714:56
	3768:219
600p:
	36

...

	60:125, 205, 485
	68:4
	69:4
	70:4
	71:4
	72:4
	73:4
	74:4
	75:4
	76:4
	77:4, 9
	79:31, 54, 254
	82:1
	89:16, 64, 146
	90:13
	92:111
	103:13, 77, 321
	105:4, 84, 134
	115:202, 268
	118:50
	129:1219
	130:898
	133:1377
	134:72, 119, 158, 630, 660
	135:705
	136:538
	137:6, 1181
	138:178, 240, 389, 697
	139:252, 882
	140:434, 658, 973
	141:1220
	143:34, 268
	146:540
	151:227
	156:82
	164:26, 60
	165:53
	166:3, 4
	167:4
	168:4
	169:4
	170:4
	171:4, 137, 292
	172:4, 235
	173:4
	174:4
	175:4, 184
	176:4
	177:4, 85, 189, 316
	178:4
	179:4
	180:4
	181:4
	182:4, 14, 155
	183:4
	184:4, 284
	185:4
	186:47, 78, 613, 664, 725, 782, 900, 981
	199:84
	200:338, 373, 419, 451, 471, 501, 525, 546, 1297
	203:5, 10, 65, 85, 135
	205:4
	206:4
	207:4
	208:4
	212:22
	213:56, 84, 235, 255
	222:112, 156
	241:14
	247:4, 17, 37, 56, 144
	248:180, 286
	250:13
	251:257
	255:51
	259:32, 74, 135
	262:754
	265:252, 414, 645
	268:12, 280, 351, 410, 503
	270:62, 159
	273:447, 513
	274:4
	275:4
	276:4
	277:4
	278:4
	279

	3908:753
	3910:266, 281, 724, 885
	3915:457
	3925:1114
	3929:827
	3933:15, 682
	3935:18
	3936:20
	3947:672
viewer:
	56:580, 611
	3369:204
	3910:704
viewpoint:
	16:8
	3354:5
	3636:9
vignett:
	57:291
	3639:975
	3865:405
vigor:
	56:753
	94:304
	248:819
	307:453
	327:228
	335:594
	366:996
	3351:127
	3415:387
	3546:47
	3567:394
	3638:338
	3655:96
	3792:76
	3915:974
vigour:
	199:7
	3788:455
vii:
	3502:137
	3600:247
vike:
	3824:139
vila:
	3786:40, 276
villa:
	342:215
	3435:860
villag:
	16:187
	58:139
	110:18
	194:346, 411
	196:139
	218:4, 537, 550
	303:54
	365:90
	3344:393
	3395:414
	3400:96
	3444:969, 1079
	3543:174
	3724:2
	3943:10
villasana:
	3547:74, 175, 230
vimto:
	141:1315
	351:1316
	3693:1486
vincent:
	129:256, 398
	342:153, 166
vine:
	3400:108
	3640:307
	3861:69
vineyard:
	3861:108, 134
vinho:
	3782:797
vintag:
	3861:2, 77, 130, 165
viola:
	3398:94
violat:
	3401:806
	3421:71
	3450:488
	3761:297
	3815:166, 195
violenc:
	109:36
	127:510
	147:6
	218:513
	227:95
	232:10
	286:37
	290:300

	371:7, 69
	3370:756
	3389:39
	3391:5, 7
	3446:1029
	3458:139
	3461:370
	3492:5
	3522:56
	3541:5
	3594:66
	3757:417
	3781:506
	3852:227
	3915:959
	3931:287, 349
wider:
	35:408
	38:6
	40:137
	115:84
	126:162
	151:282
	184:198, 422
	202:203
	206:116
	216:165
	308:79
	318:103
	335:274
	358:407
	366:859, 861
	372:805
	375:156
	3444:952
	3449:1236
	3516:11
	3645:1159, 1275
	3678:20
	3693:655
	3706:326
	3728:157, 828
	3781:728
	3793:1194
	3906:13, 913
	3910:901
	3922:953
widespread:
	12:397
	53:162
	130:38
	138:561
	207:48
	251:170
	3531:180
	3678:40
	3692:377
	3757:148
	3793:951
	3885:37
	3915:198
	3917:378, 752
	3918:765
widmann:
	3567:629
widow:
	3446:1255
width:
	3917:551
wiedig:
	3929:91
wiegman:
	3565:206, 232
wield:
	3409:167
	3891:386
wienerberg:
	3944:146
wiesbaden:
	3666:221
wife:
	52:179
	58:3, 132, 185
	127:3, 468
	196:3, 132, 185
	272:255
	368:461
	3335:141
	3340:192
	3366:560
	3644:167
	3729:704
	3894:107
wig:
	260:138
	3366:1015
wigan:
	73:11
wiggin:
	247:101
	3795:34
wil:
	54

	3434:606, 910
	3436:209, 571
yield:
	20:136, 247
	21:176, 193, 339, 354, 464, 763
	42:142
	45:159, 172, 200
	94:322, 350, 371
	128:135, 148
	140:697
	141:693
	151:266, 279, 375, 416, 429
	169:1238
	241:167
	244:173, 284
	248:284, 296, 637, 715, 752, 927, 936
	262:836
	305:345
	313:362
	314:121, 139, 146, 165, 179, 199, 207
	315:172, 395, 902, 912
	3359:373
	3366:392
	3370:1419
	3405:388
	3459:508
	3468:40, 58, 280, 569
	3559:133, 146
	3578:266, 288
	3584:284
	3593:108
	3596:256
	3607:335
	3644:1333
	3701:79, 299, 458, 483, 639, 659
	3774:134, 147
	3806:81, 133, 146
	3830:118
	3849:239
	3937:847
	3945:6, 117
yitzhak:
	223:294
	288:104
	305:331
	3549:173
	3762:11
ymp:
	3927:132, 880
ymp2e:
	3927:292
yoghurt:
	132:324
yoichi:
	3570:219
yokohama:
	3693:762
	3848:16, 93, 183, 230, 290
yonemoto:
	135:393, 430, 1094
york:
	13:30
	14:40, 98, 296
	15:518
	56:167
	101:10
	118:261
	128:2, 42, 72, 188
	144:15
	154:316
	161:18, 104
	171:371
	181:7
	187:166, 183
	188:356
	216:48
	220:66
	245:35, 51

{'0': {14: [89, 193, 208, 219],
  15: [18, 38, 43, 505],
  21: [274, 284],
  23: [250],
  37: [23, 84, 206, 226],
  59: [16,
   194,
   218,
   261,
   307,
   364,
   501,
   829,
   908,
   945,
   1002,
   1048,
   1110,
   1147,
   1209],
  118: [220],
  128: [185],
  135: [335, 353],
  137: [1226, 1228],
  144: [266],
  145: [384, 545, 600],
  146: [24,
   356,
   359,
   372,
   374,
   376,
   398,
   411,
   450,
   473,
   489,
   502,
   515,
   528,
   541,
   543,
   554,
   556,
   558,
   581,
   583,
   594,
   596,
   607,
   609,
   634,
   647,
   649,
   651,
   689,
   701,
   703],
  216: [68],
  217: [35, 187],
  222: [128],
  268: [318, 324, 330, 331, 359, 365, 391, 405, 459, 466],
  275: [346, 399, 419, 433],
  287: [823,
   874,
   879,
   881,
   886,
   899,
   900,
   909,
   913,
   914,
   928,
   942,
   980,
   1004,
   1018,
   1020,
   1023,
   1034,
   1047,
   1048,
   1059,
   1061,
   1067,
   1072,
   1074,
   1107,
   1119,
   1127,
   1139,
   1

<h2>Running search on index</h2>

Build a module that allows the following: 
- load index into memory 
- apply Boolean search (AND, OR, and NOT) 
- apply phrase search 
- apply proximity search

Run the following queries in the following file, and report the list of retrieved documents for each query. Discuss your results with your colleagues and try to find where is the problem if there are difference in answers.
Think of the following: 

- If the index is very large, what would be the best way to save the index, and how it should be loaded into memory for search later? 
- What if the number of document is very large, and terms appears in documents 100000001 to 10010000. Is there a more effecient way to save document numbers? (read on Delta Encoding) . 

In [110]:
# load index into memory
inverted_index = build_inverted_index('./collections/trec.sample.xml')

0:
	14:89, 193, 208, 219
	15:18, 38, 43, 505
	21:274, 284
	23:250
	37:23, 84, 206, 226
	59:16, 194, 218, 261, 307, 364, 501, 829, 908, 945, 1002, 1048, 1110, 1147, 1209
	118:220
	128:185
	135:335, 353
	137:1226, 1228
	144:266
	145:384, 545, 600
	146:24, 356, 359, 372, 374, 376, 398, 411, 450, 473, 489, 502, 515, 528, 541, 543, 554, 556, 558, 581, 583, 594, 596, 607, 609, 634, 647, 649, 651, 689, 701, 703
	216:68
	217:35, 187
	222:128
	268:318, 324, 330, 331, 359, 365, 391, 405, 459, 466
	275:346, 399, 419, 433
	287:823, 874, 879, 881, 886, 899, 900, 909, 913, 914, 928, 942, 980, 1004, 1018, 1020, 1023, 1034, 1047, 1048, 1059, 1061, 1067, 1072, 1074, 1107, 1119, 1127, 1139, 1191, 1193, 1211, 1258, 1269, 1301, 1324, 1468, 1515, 1526, 1563, 1571, 1618, 1652, 1655, 1666, 1678, 1685, 1688, 1694, 1699, 1710, 1716, 1721, 1734, 1747, 1753, 1760, 1802, 1806, 1811, 1813, 1836, 1861, 1872, 1884, 1917, 1942, 1946, 1952, 1953, 1964, 1970, 1974, 1975, 1982, 1984, 1989, 2002, 2021, 2046, 2054, 2080, 

	3402:140
	3414:366
	3417:1035
	3419:154
	3435:7
	3441:711
	3445:281
	3461:487
	3468:179, 247, 274
	3475:111
	3478:58
	3493:321
	3504:453
	3521:6, 18, 103
	3527:145
	3535:161
	3542:39
	3552:30
	3559:126
	3569:780
	3570:835
	3577:13
	3578:164
	3582:22
	3584:69
	3598:180, 203
	3606:189
	3622:408
	3625:144
	3631:30
	3639:761
	3642:1059, 1151
	3661:33
	3662:109
	3667:56
	3693:394
	3694:614
	3695:738, 961
	3697:477
	3699:259
	3701:66, 371
	3710:65
	3720:269
	3723:15
	3726:600, 635, 797
	3729:903
	3757:247, 415
	3776:438
	3783:632
	3785:790
	3786:1119
	3789:176, 181
	3792:149, 664, 874
	3793:623, 935
	3796:264
	3803:142
	3811:350
	3820:62
	3822:325
	3826:699
	3827:139
	3831:61
	3837:77, 144
	3845:53
	3878:81
	3916:47
	3917:657
	3924:9
	3926:393
	3939:693
150:
	45:120
	136:835, 847
	197:429
	244:241
	273:347
	367:187
	3327:166
	3467:64
	3755:32
	3889:136
	3895:407
	3945:37, 72, 102
150bn:
	280:164
150m:
	18:74
	36:117, 127
	141:975
	151:259
	185:47
	188:808
	245:131
	354:499
	3333:248
	3382:1

	3663:196
	3741:92
	3783:601
	3794:216
	3796:350
	3800:245
	3828:287
	3833:481
	3837:113
	3877:272
	3891:183
	3928:408
2000:
	46:236, 689
	135:358, 444
	262:1172
	307:212
	351:1500
	3323:322
	3344:27, 87, 172, 429
	3411:560, 761
	3417:451
	3434:836
	3444:601
	3667:97
	3786:570
	3803:31
	3830:64, 100, 160
	3925:56
	3936:726
2001:
	21:363
	151:277
	313:604
	351:1672
	3468:538
	3701:75
	3802:138
2002:
	40:86
	140:1115
	351:1435, 2040
2003:
	21:30
	3417:520
	3693:1597
	3701:281
2004:
	351:2033
2005:
	188:486
	351:1334
	3417:553
2006:
	351:1522
	3468:196
2007:
	351:1482
	3701:282
2008:
	313:466
2009:
	351:1938
200bn:
	357:28
200m:
	18:76
	36:119
	151:53
	155:113
	201:208
	245:58
	312:304
	313:584
	3386:15
	3389:15
	3406:694
	3409:357
	3435:592
	3450:29
	3484:29
	3571:251
	3578:240
	3700:129
	3716:1190
	3871:346
	3928:506
	3931:831
200mph:
	371:85
200mw:
	3649:145
200p:
	3459:257
	3630:40
201:
	3566:128
2010:
	19:128
	3410:303
	3412:762
	3655:180, 278
2011:
	313:610
	3781:756
2012:
	351:1458

	3732:116
	3785:291
	3789:7
	3810:14, 89
	3937:699
340:
	3323:319
	3922:618
340bn:
	3443:667
340m:
	144:66
	3435:916
340p:
	3826:393
341264:
	368:910
342:
	3796:492
342317:
	368:917
342m:
	3816:107
3438:
	3911:769
344:
	3530:848
345:
	356:112
	3721:31
346:
	17:465
347:
	3530:859
	3838:259
349:
	3644:1279
34bn:
	3593:262
	3808:181, 237
34m:
	25:37
	3343:60
	3482:331
	3611:34
	3846:137
34p:
	3616:64
35:
	15:237
	16:601
	21:367
	32:36
	76:19
	79:236
	98:156
	138:704, 759
	144:86, 608
	146:362, 407, 635
	163:45
	189:196
	197:186
	210:185
	244:279
	312:632
	327:774
	3327:330
	3361:299
	3370:629
	3405:715
	3414:261
	3417:852
	3435:928
	3439:346, 714
	3521:45, 150
	3567:655
	3587:107
	3599:162
	3609:74
	3611:36
	3629:190
	3643:811
	3644:414, 510, 684, 1255
	3649:97
	3666:200
	3674:524
	3686:10
	3694:568
	3696:330
	3756:134, 202
	3758:165
	3774:114
	3790:220
	3791:728
	3808:7, 23
	3819:44
	3903:11
	3914:582
	3936:1012
350:
	55:1012
	125:169
	133:195
	346:174
	361:535
	3399:273
	3435:798
	3442:

	3695:128
	3698:198
	3702:30
	3716:371, 1183
	3718:153
	3726:1768
	3760:192
	3786:182, 447
	3788:29, 340, 352
	3792:230, 851, 875
	3807:30
	3820:107
	3821:97
	3823:10
	3833:45, 50
	3900:157, 195
	3913:1007
	3919:358
	3927:146
	3933:194, 331
	3935:1145
5ew:
	254:270
5m:
	14:425
	16:326
	24:34, 330
	27:64
	34:316
	135:436
	138:326
	141:25
	144:641, 675
	148:297
	156:44
	165:383
	169:298, 674, 699
	173:568
	175:28
	178:230
	181:81, 84
	184:73
	186:515
	241:1053
	247:50
	270:58, 93
	272:629
	285:334
	296:208
	306:445
	324:55
	341:509
	342:192
	345:22
	350:16
	367:91, 544
	369:663
	370:614
	372:104, 851
	374:373, 544
	375:415, 777
	3331:321
	3336:75, 324
	3337:92
	3338:129
	3339:137
	3342:377
	3354:545
	3369:624, 1027
	3387:292
	3396:336
	3398:251
	3400:152
	3403:545
	3434:825
	3439:643
	3445:229
	3450:547
	3459:400, 415, 860, 916
	3460:289, 437
	3469:37
	3474:24
	3477:56
	3484:468
	3487:116
	3502:68
	3513:87
	3523:53
	3526:284
	3563:324
	3582:210
	3589:55
	3593:13, 30
	3594:91
	3596:289
	3

...

	3925:138
	3931:805
	3933:458, 883
	3938:617
	3939:82, 170
	3947:514
turnabout:
	307:89
turnaround:
	3860:216
	3937:637
turner:
	3565:137
	3640:186
turnkey:
	103:28
turnout:
	69:90
	226:689
	356:95
turnov:
	14:94, 239, 422
	16:315, 340
	32:28
	34:309
	35:314
	136:79
	141:888, 914
	144:526, 620, 792, 837, 915
	145:304, 347, 550, 712, 828
	146:88
	163:157
	171:206, 233
	172:245
	175:72
	184:63
	272:626
	273:424
	280:55, 176, 231, 265
	312:542
	319:42
	322:47
	329:116, 218
	357:245
	370:574
	374:824
	3324:55, 78, 150, 195
	3326:15, 90, 115
	3332:163
	3333:176
	3336:52
	3337:181
	3341:70
	3342:42, 95, 128, 281
	3343:55
	3400:168
	3401:847
	3439:911
	3443:939
	3458:220, 293
	3459:198, 563, 855, 912
	3460:138, 272, 434
	3480:185
	3483:321
	3506:133
	3566:78
	3569:276
	3570:580, 695, 746
	3580:210
	3589:31, 197
	3600:99
	3601:38, 77, 136
	3605:240, 308
	3606:72, 120, 145
	3607:36
	3608:21
	3611:30
	3613:90
	3614:27
	3616:40
	3618:31
	3621:131
	3625:71
	3628:88, 133
	3629:212
	3667:63
	3692:23

	3833:41
	3844:287
	3847:29
	3868:115
	3876:386
valuabl:
	41:19
	133:1394
	158:221
	201:172
	203:58
	226:839
	3381:179
	3567:429
valuat:
	32:150
	92:120, 175, 205, 216, 241
	145:278
	154:412
	165:164
	183:123, 240
	226:683, 747
	321:183
	327:984
	3401:378
	3404:414
	3528:250
	3531:313
	3533:430, 601, 603
	3561:289, 328, 343
	3624:149, 182
	3644:250, 389, 482, 736, 858
	3728:196
	3822:275
valuer:
	183:29
	3463:628, 643, 665
	3528:253
	3624:122
	3644:8, 33, 51, 118, 217, 237, 453, 614, 650, 907, 1119, 1189, 1209, 1246, 1347
valv:
	140:476
	3573:120
van:
	56:828
	214:262
	3386:31
	3640:525, 633, 668
	3918:790
vanadium:
	3572:175
vancouv:
	244:142
vanguard:
	48:78, 658
	60:75
	134:389
vanish:
	3366:518
	3922:111
vaniti:
	46:370
vard:
	3824:2, 7, 41, 132
varga:
	3785:723
vari:
	131:530
	132:227
	138:107
	139:400
	169:17
	206:136
	226:748
	252:284
	3354:531
	3366:1028
	3400:85
	3411:908
	3513:105
	3532:102
	3580:404
	3643:507
	3654:518
	3933:640
variabl:
	16:582, 651
	3826:314
varian:
	349:4

	368:515
	3366:579
waiv:
	262:551
	3482:264
wake:
	12:98
	14:10
	21:134, 554
	134:110
	3331:107
	3357:19
	3370:1382
	3413:141
	3432:125
	3441:273
	3449:877
	3459:1274
	3460:27
	3672:319
	3693:307, 647
	3694:499
	3701:693
	3768:176
	3775:84
	3794:25
wakefield:
	3530:831
wakeham:
	3416:235, 309, 645
	3876:166
waldegrav:
	252:336
waldron:
	129:453, 502
wale:
	80:62
	83:28
	90:223
	94:128
	96:14, 138
	125:329
	165:357
	241:1524
	273:10
	275:41, 229, 431
	366:64, 200, 295, 625, 850
	368:190, 476, 477, 594
	369:21, 174, 433, 483
	370:55, 94, 161, 196, 331, 340, 357, 378, 415, 781, 798, 869, 885, 894, 915, 943, 965
	371:32, 101, 189, 591, 879
	372:27, 87, 146
	373:45
	374:692, 835
	375:148, 237, 253, 575, 840
	3411:154
	3418:329
	3459:1084, 1105
	3461:344
	3504:265
	3520:11
	3524:190, 243
	3525:135
	3532:15, 74, 208, 240, 257, 349
	3533:526, 1040
	3561:170, 406
	3649:11
	3651:10
	3654:585
	3750:3
	3928:404, 933
walesa:
	225:125
	3394:20
	3660:479
	3760:335
	3768:2, 4, 98, 141, 268, 312
	3856:

	58:524
	140:481
	196:524
	264:424
weinberg:
	3502:118
weir:
	103:353, 361
	197:411
	251:106, 438
weird:
	266:403
weiss:
	327:592, 629, 662, 1065
welbeck:
	3826:77, 96
welcom:
	90:154
	113:37
	126:430
	145:9
	191:59
	222:107
	225:139
	3463:534
	3483:334
	3503:1256
	3528:258, 332
	3541:25
	3625:326
	3632:11, 63
	3641:685
	3647:168
	3666:114
	3699:98
	3714:281
	3724:910
	3932:250
weld:
	56:517, 597
	129:736
	135:229, 323
	3421:204
welder:
	56:50
welfar:
	252:73
	275:356
	328:993
	3437:183
	3535:28
	3592:92
	3704:92
	3793:596
well:
	183:69, 111, 177
	193:9
	351:1794
	3362:435
	3642:254
	3747:75
wellesley:
	3740:250
wellhead:
	3385:71, 82
wellington:
	141:757, 775
	164:38
	3491:290, 379, 454, 486
wellspr:
	129:413
welsh:
	241:233
	368:320, 446, 466, 499, 506, 524, 536, 545, 553, 571, 577
	369:55, 89, 298
	370:151, 169, 198, 222, 443, 557, 906, 976
	371:120, 566, 768
	372:9, 83, 415, 913, 948
	373:9, 15, 38
	374:178, 588, 682, 730, 742
	3505:113
	3525:140
	3532:173, 194, 333
weltetho:
	3360

	3792:1072
wound:
	58:312
	105:7
	196:312
	239:4
	326:33
	3330:19
	3453:10
woven:
	58:226
	196:226
wow:
	338:8
wpp:
	141:1087
	3623:57
wrack:
	266:482
	3496:174
wrangl:
	3698:342
	3926:830
wrap:
	358:562
wrath:
	42:48
	3383:167
	3771:470
wreath:
	362:14
wreck:
	110:4
	3396:37
	3671:237
wreckag:
	110:4
wrest:
	3891:371
wrestl:
	337:469
	3404:60
	3865:438
wri:
	3366:875
writ:
	3524:33
	3644:372
write:
	14:35
	18:29
	21:812
	33:180
	46:762
	57:65, 238
	59:30, 514, 972
	80:27
	102:37
	103:352
	107:36
	108:39
	114:36
	141:1139
	144:26
	145:25
	152:43
	156:28
	159:18
	164:34
	170:35
	176:38
	211:18
	212:38
	222:38
	227:31
	246:45
	257:32
	270:167
	287:734
	291:201, 224
	294:31
	316:26
	317:49, 200, 288
	326:9, 16, 73, 84
	330:10, 13
	337:266
	3324:32
	3326:20
	3347:70
	3357:52
	3360:495
	3363:242
	3374:252
	3391:15
	3401:803
	3438:29
	3442:22
	3445:43
	3458:391
	3460:35
	3471:32
	3472:148
	3473:37
	3474:27
	3481:58
	3482:9, 10
	3486:53
	3493:410
	3500:102
	3507:30
	3512:28, 70
	3513:37
	3516

In [111]:
# parse queries, assuming they only contain two terms

q = '"Scotland and national" AND NOT mother'
q = re.split(" +(AND|OR) +",q)

q

['"Scotland and national"', 'AND', 'NOT mother']

In [232]:
# Preprocess query in the same way you processed the text
# This will return a list of phrases and boolean words
# we assume there are only two terms in this query
# term1 AND/OR/NOT/AND NOT/OR NOT term2
def preprocess_query(query, stopword_file='./englishST.txt', stemming=True, stopping=True):
    
    # first check if the query is a proximity search
    if query[0] == '#':
        # split between # and ( - this will give us the proximity number
        open_par_sign_idx = query.index('(')
        close_par_sign_idx = query.index(')')
        proximity_number = int(query[1:open_par_sign_idx])
        
        # preprocess what is inside the paranthesis
        q = query[open_par_sign_idx+1:close_par_sign_idx].replace(",", " ").split()
        
        q[0] = preprocess_word(q[0], stopword_file, stemming, stopping)
        q[1] = preprocess_word(q[1], stopword_file, stemming, stopping)
    
        return (q[0], proximity_number, q[1])
    
    return_list = list()
    
    q = re.split(" +(AND|OR) +", query)
    
    for phrase in q:
        negated = False
        
        if phrase in ['AND', 'OR']:
            #print("return list before append: " + str(return_list))
            return_list.append(phrase)
            #print("Found connection word, return_list = " + str(return_list))
            
        else:
            # if the phrase is not a connection word, it might still contain NOT
            if phrase[:3] == 'NOT':
                original_phrase = phrase[4:] # excluding the extra space
                #print("Found NOT, og phrase = " + original_phrase)
                negated = True
            else:
                original_phrase = phrase

            # each phrase can be a single word or more words
            if original_phrase[0] == '"':
                # this means we are dealing with more words
                #print("We have a phrase = ", phrase)
                words = original_phrase.split()
                #print(words)
                for i in range(len(words)):
                    words[i] = preprocess_word(words[i], stopword_file, stemming, stopping)
                if negated:
                    final_phrase = 'NOT ' + " ".join(words)
                    #print("Final phrase: " + final_phrase)
                    return_list.append(final_phrase)
                else:
                    #print(" ".join(words))
                    #print("return list before append: " + str(return_list))
                    return_list.append(" ".join(words))
                #print("Return list after phrase: " + str(return_list))
            else:
                # we are lookin at a single word
                original_phrase = preprocess_word(original_phrase, stopword_file, stemming, stopping)
                if original_phrase != "":
                    if negated:
                        return_list.append('NOT ' + original_phrase)
                    else:
                        return_list.append(original_phrase)
                #print("Return list after word: " + str(return_list))
    
    return return_list

def preprocess_word(word, stopword_file='./englishST.txt', stemming=True, stopping=True):
            
    # eliminate special characters
    word = re.sub(r"[^\w\s]|_", "", word)

    # lowercase
    word = word.lower()

    # stopwords
    
    if stopping:
        # read stopword file
        with open(stopword_file) as f:
            stopwords = f.read().split()

        f.close()
        
        if word in stopwords:
            return ""

    # stemming
    if stemming:
        word = stem(word)

    return word

In [233]:
q = '"Scotland and national" AND NOT mother'
print(preprocess_query(q, stopping=True, stemming=True))

['scotland  nation', 'AND', 'NOT mother']


In [242]:
# now we process the query
# when we encounter a phrase, we do a phrase search
# here we receive a preprocessed phrase
# do we only assume we have two words too?

def process_phrase_query(phrase, prox=1):
    
    negated = False
    
    # first check if this is a NOT phrase
    if phrase[:3] == 'NOT':
        negated = True
        phrase = phrase[4:] 
    
    words = phrase.split()
    inverted_index_rlv = dict()
    
    if len(words) == 1:
        return process_word_query(phrase, negated)
    
    for word in words:
        inverted_index_rlv[word] = inverted_index[word]
        
    stop_search = False
    num_docs_word1 = len(inverted_index_rlv[words[0]])
    num_docs_word2 = len(inverted_index_rlv[words[1]])
    
    iterable_keys_word1 = iter(inverted_index_rlv[words[0]])
    iterable_keys_word2 = iter(inverted_index_rlv[words[1]])
    
    document_list = list()
    
    next_doc_word1 = None
    next_doc_word2 = None
    
    try:
        next_doc_word1 = next(iterable_keys_word1)
        next_doc_word2 = next(iterable_keys_word2)
    except StopIteration:
        print("One of the words in your query is not in our database!")
        stop_search = True
    
    
    while not stop_search:

        if next_doc_word1 == next_doc_word2:
            #print("Found occurrence in the same document = " + str(next_doc_word1))
            # compare all the positions in these files
            # and see if you find two that are next to each other
            # these should be lists
            postings_word1 = inverted_index_rlv[words[0]][next_doc_word1]
            postings_word2 = inverted_index_rlv[words[1]][next_doc_word2]

            k = 0
            l = 0

            while k < len(postings_word1) and l < len(postings_word2):
                #print("k = {0}, l = {1}".format(k,l))
                if postings_word1[k] < postings_word2[l]:
                    if abs(postings_word1[k] - postings_word2[l]) <= prox:
                        # we have found a phrase! 
                        # return this document
                        document_list.append(next_doc_word1)
                        
                        # set k and l to the length of the postings
                        # once we find one occurrence in the document we add it to the results anyway
                        # so there is no need to check further into the document
                        k = len(postings_word1)
                        l = len(postings_word2)
                    else:
                        # the postings are sorted so we increase k
                        k += 1
                elif postings_word1[k] > postings_word2[l]:
                    if abs(postings_word1[k] - postings_word2[l]) <= prox:
                        # we have found a phrase! 
                        # return this document
                        document_list.append(next_doc_word1)
                        k = len(postings_word1)
                        l = len(postings_word2)
                    else:
                        l += 1
                else:
                    # if both postings are the same (don't see how this could happen)
                    # increase both k and l
                    k+=1
                    l+=1

            try:
                # update the document numbers
                next_doc_word1 = next(iterable_keys_word1)
                next_doc_word2 = next(iterable_keys_word2)
            except StopIteration:
                stop_search = True

        elif next_doc_word1 < next_doc_word2:
            try:
                next_doc_word1 = next(iterable_keys_word1)
            except StopIteration:
                stop_search = True

        else:
            try:
                next_doc_word2 = next(iterable_keys_word2)
            except StopIteration:
                stop_search = True
    
    if negated == False:
        return document_list
    else:
        return process_not_query(document_list)

In [243]:
process_phrase_query('incom tax')

[65, 92, 282, 3405, 3441, 3449, 3562, 3706, 3734]

In [244]:
def process_word_query(word, negated=False):
    relevant_docs = inverted_index[word].keys()
    
    if negated == False:
        return list(relevant_docs)
    else:
        return process_not_query(list(relevant_docs))

In [245]:
def process_not_query(list_of_docs):
    # the way we process the NOT queries is 
    # we take the relevant docs and return all keys 
    # apart from the ones that contain the word/phrase
    
    # get the list of all documents
    # TODO - you can save this globally 
    all_docs = set()
    for word in inverted_index.keys():
        for docNo in inverted_index[word].keys():
            all_docs.add(docNo)
    
    list_of_docs = set(list_of_docs)
    
    relevant_docs = all_docs.difference(list_of_docs)
    
    return sorted(list(relevant_docs))

In [246]:
def process_boolean_query(term1, operator, term2):
    
    # term1 and term2 can be phrases too
    documents_term1 = process_phrase_query(term1)
    documents_term2 = process_phrase_query(term2)
    
    if operator == 'AND':
        relevant_documents = set(documents_term1).intersection(set(documents_term2))

    else:
        # operator is 'OR' so we return the union
        relevant_documents = set(documents_term1).union(set(documents_term2))
    
    return sorted(list(relevant_documents))

In [247]:
process_boolean_query('incom', 'OR', 'tax')

[3,
 14,
 16,
 23,
 24,
 32,
 33,
 34,
 39,
 41,
 42,
 43,
 46,
 65,
 92,
 106,
 112,
 113,
 125,
 141,
 144,
 146,
 161,
 163,
 168,
 170,
 171,
 172,
 173,
 175,
 177,
 178,
 184,
 185,
 186,
 190,
 216,
 226,
 228,
 241,
 248,
 257,
 262,
 268,
 270,
 282,
 287,
 304,
 313,
 314,
 315,
 316,
 317,
 319,
 322,
 325,
 326,
 328,
 329,
 351,
 357,
 360,
 361,
 366,
 370,
 375,
 3324,
 3327,
 3329,
 3331,
 3332,
 3333,
 3336,
 3337,
 3341,
 3342,
 3343,
 3345,
 3347,
 3374,
 3387,
 3388,
 3390,
 3396,
 3397,
 3401,
 3403,
 3404,
 3405,
 3407,
 3409,
 3412,
 3415,
 3417,
 3420,
 3437,
 3439,
 3441,
 3443,
 3444,
 3449,
 3460,
 3469,
 3470,
 3472,
 3473,
 3474,
 3475,
 3480,
 3481,
 3482,
 3490,
 3494,
 3495,
 3498,
 3503,
 3504,
 3511,
 3519,
 3525,
 3527,
 3528,
 3529,
 3530,
 3531,
 3532,
 3533,
 3535,
 3537,
 3542,
 3543,
 3548,
 3561,
 3562,
 3563,
 3567,
 3569,
 3580,
 3582,
 3586,
 3589,
 3590,
 3591,
 3592,
 3593,
 3595,
 3596,
 3597,
 3599,
 3602,
 3604,
 3606,
 3607,
 3608,
 361

In [264]:
# Finally, we build a reader that decides what to do with the queries
def read_query(query, stopword_file='./englishST.txt', stopping=True, stemming=True):
    
    ppq = preprocess_query(query)
    
    if isinstance(ppq, list):
        # we have either a simple search or a boolean query
        if 'AND' in ppq or 'OR' in ppq:
            return process_boolean_query(ppq[0], ppq[1], ppq[2])
        else:
            return process_phrase_query(" ".join(ppq))
    elif isinstance(ppq, tuple):
        word1 = ppq[0]
        prox = ppq[1]
        word2 = ppq[2]
        
        phrase = " ".join([word1, word2])
        return process_phrase_query(phrase, prox)

In [265]:
read_query("Scotland")

[16,
 94,
 96,
 143,
 272,
 351,
 370,
 3330,
 3334,
 3336,
 3338,
 3376,
 3485,
 3504,
 3505,
 3532,
 3533,
 3561,
 3565,
 3629,
 3654,
 3820,
 3826,
 3932,
 3938]

In [266]:
with open('./queries.lab2.txt', 'r') as f:
    queries = f.read().splitlines()
f.close()

for line in queries:
    query = line[4:]
    
    print(line[:4])
    print(read_query(query))

q1: 
[16, 94, 96, 143, 272, 351, 370, 3330, 3334, 3336, 3338, 3376, 3485, 3504, 3505, 3532, 3533, 3561, 3565, 3629, 3654, 3820, 3826, 3932, 3938]
q2: 
[30, 55, 59, 145, 160, 272, 374, 3463, 3639, 3782, 3788, 3906, 3909, 3910, 3917, 3930]
q3: 
[16, 28, 31, 51, 92, 97, 131, 135, 136, 138, 140, 169, 195, 197, 218, 242, 256, 274, 276, 325, 3325, 3342, 3361, 3370, 3387, 3397, 3403, 3410, 3411, 3413, 3418, 3437, 3438, 3461, 3494, 3504, 3521, 3531, 3532, 3533, 3561, 3598, 3623, 3654, 3660, 3662, 3668, 3693, 3700, 3716, 3720, 3724, 3734, 3745, 3788, 3805, 3828, 3867, 3869, 3876, 3886, 3895, 3896, 3907, 3918, 3921, 3930, 3935]
q4: 
[113, 309, 354, 3374, 3674, 3678]
q5: 
[3, 14, 16, 23, 24, 32, 33, 34, 39, 41, 42, 43, 46, 65, 92, 106, 112, 113, 125, 141, 144, 146, 161, 163, 168, 170, 171, 172, 173, 175, 177, 178, 184, 185, 186, 190, 216, 226, 228, 241, 248, 257, 262, 268, 270, 282, 287, 304, 313, 314, 315, 316, 317, 319, 322, 325, 326, 328, 329, 351, 357, 360, 361, 366, 370, 375, 3324, 3327, 332

In [267]:
i = "#10(income, tax)"
text = re.sub(r"[^\w\s]|_", " ", i).split()

In [268]:
text

['10', 'income', 'tax']

In [270]:
stem('10')

'10'